## 1 - Extracting Tesla Stock Data Using yfinance

In [1]:
!pip install pandas
!pip install requests
!pip install bs4
!pip install html5lib
!pip install lxml
!pip install plotly

In [2]:
import yfinance as yf
import pandas as pd
import json

In [51]:
tesla = yf.Ticker("TSLA")

In [52]:
tesla_info = tesla.info
print(json.dumps(tesla_info, indent=4))

{
    "address1": "1 Tesla Road",
    "city": "Austin",
    "state": "TX",
    "zip": "78725",
    "country": "United States",
    "phone": "512 516 8177",
    "website": "https://www.tesla.com",
    "industry": "Auto Manufacturers",
    "industryKey": "auto-manufacturers",
    "industryDisp": "Auto Manufacturers",
    "sector": "Consumer Cyclical",
    "sectorKey": "consumer-cyclical",
    "sectorDisp": "Consumer Cyclical",
    "longBusinessSummary": "Tesla, Inc. designs, develops, manufactures, leases, and sells electric vehicles, and energy generation and storage systems in the United States, China, and internationally. The company operates in two segments, Automotive; and Energy Generation and Storage. The Automotive segment offers electric vehicles, as well as sells automotive regulatory credits; and non-warranty after-sales vehicle, used vehicles, body shop and parts, supercharging, retail merchandise, and vehicle insurance services. This segment also provides sedans and sport ut

In [53]:
tesla_share_price_data = tesla.history(period="max")

In [54]:
tesla_share_price_data.reset_index(inplace=True)

In [55]:
tesla_share_price_data.head()

Date      Open      High       Low     Close  \
0 2010-06-29 00:00:00-04:00  1.266667  1.666667  1.169333  1.592667   
1 2010-06-30 00:00:00-04:00  1.719333  2.028000  1.553333  1.588667   
2 2010-07-01 00:00:00-04:00  1.666667  1.728000  1.351333  1.464000   
3 2010-07-02 00:00:00-04:00  1.533333  1.540000  1.247333  1.280000   
4 2010-07-06 00:00:00-04:00  1.333333  1.333333  1.055333  1.074000   

      Volume  Dividends  Stock Splits  
0  281494500        0.0           0.0  
1  257806500        0.0           0.0  
2  123282000        0.0           0.0  
3   77097000        0.0           0.0  
4  103003500        0.0           0.0

## 2 - Extracting Tesla Revenue Data Using Webscraping

In [56]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import time

In [57]:
url = "https://finance.yahoo.com/quote/TSLA/financials/"
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36',
    'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
    'Accept-Language': 'en-US,en;q=0.5',
    'Referer': 'https://finance.yahoo.com/'
}

data = requests.get(url, headers=headers).text

In [58]:
print(data)

<!doctype html>
<html lang="en-US" theme="auto" data-color-theme-enabled="true" data-color-scheme="auto" class="desktop neo-green dock-upscale">
    <head>
        <meta charset="utf-8" />
        <meta name="oath:guce:consent-host" content="guce.yahoo.com" />
        <link rel="preconnect" href="//s.yimg.com" crossorigin="anonymous"><link rel="preconnect" href="//geo.yahoo.com"/><link rel="preconnect" href="//query1.finance.yahoo.com"/><link rel="preconnect" href="//query2.finance.yahoo.com"/><link rel="preconnect" href="//consent.cmp.oath.com"/><link rel="preload" href="/__rapidworker-1.2.js" as="worker"/><link rel="preconnect" href="https://s.yimg.com/uc/finance/webcore/js/_staticFinProtobuf.adb9bf9ae7922cf2dccf.js"/><link rel="preconnect" href="https://cdn.jsdelivr.net/npm/protobufjs@7.1.2/dist/minimal/protobuf.min.js"/><script>window.finNeoPageStart = Date.now();</script><script>(function(){if(!window.YAHOO){window.YAHOO={}}; window.YAHOO.context={"consent":{"allowContentPersonali

> Create Soup object

In [59]:
soup = BeautifulSoup(data, 'html.parser')

> Extract the Revenue Table

In [60]:
Revenue_table = soup.find_all("div", class_="table yf-yuwun0")[0]
Revenue_table_header = Revenue_table.find("div", class_="tableHeader yf-yuwun0")
Revenue_table_body = Revenue_table.find("div", class_="tableBody yf-yuwun0")

> Extract the columns names

In [61]:
columns = []
for row in Revenue_table.find("div", class_="tableHeader yf-yuwun0").find_all("div", class_="column"):
    columns.append(row.text)
print(columns)

['Breakdown', 'TTM ', '12/31/2024 ', '12/31/2023 ', '12/31/2022 ', '12/31/2021 ']


> Create Tesla DataFrame

In [62]:
tesla_data = pd.DataFrame(columns=columns)

> Fill Table Values

In [63]:
rows_data = []

for row in Revenue_table.find("div", class_="tableBody yf-yuwun0").find_all("div", class_="row"):
    cols = row.find_all("div", class_="column")
    breakdown = cols[0].find("div", class_="rowTitle").text.strip()
    values = [col.text.strip() for col in cols[1:]]
    rows_data.append({
        "Breakdown": breakdown,
        "TTM ": values[0] if len(values) > 0 else None,
        "12/31/2024 ": values[1] if len(values) > 1 else None,
        "12/31/2023 ": values[2] if len(values) > 2 else None,
        "12/31/2022 ": values[3] if len(values) > 3 else None,
        "12/31/2021 ": values[4] if len(values) > 4 else None
    })

tesla_data = pd.DataFrame(rows_data)
tesla_data.head()

Breakdown        TTM  12/31/2024  12/31/2023  12/31/2022   \
0      Total Revenue  92,720,000  97,690,000  96,773,000  81,462,000   
1    Cost of Revenue  76,513,000  80,240,000  79,113,000  60,609,000   
2       Gross Profit  16,207,000  17,450,000  17,660,000  20,853,000   
3  Operating Expense  10,429,000   9,690,000   8,769,000   7,021,000   
4   Operating Income   5,778,000   7,760,000   8,891,000  13,832,000   

  12/31/2021   
0  53,823,000  
1  40,217,000  
2  13,606,000  
3   7,110,000  
4   6,496,000

In [77]:
tesla_data.tail()

Breakdown        TTM  12/31/2024   \
29  Total Unusual Items Excluding Goodwill    -156,000    -684,000   
30                     Total Unusual Items    -156,000    -684,000   
31                       Normalized EBITDA  13,698,000  15,392,000   
32                      Tax Rate for Calcs           0           0   
33             Tax Effect of Unusual Items     -31,627    -136,800   

   12/31/2023  12/31/2022  12/31/2021   
29           0    -176,000      27,000  
30           0    -176,000      27,000  
31  14,796,000  17,833,000   9,598,000  
32           0           0           0  
33           0     -14,080       2,970

## 3 - Extracting GameStop Stock Data Using yfinance

In [64]:
gamestop = yf.Ticker("GME")
gamestop_info = gamestop.info
print(json.dumps(gamestop_info, indent=4))

{
    "address1": "625 Westport Parkway",
    "city": "Grapevine",
    "state": "TX",
    "zip": "76051",
    "country": "United States",
    "phone": "817 424 2000",
    "website": "https://www.gamestop.com",
    "industry": "Specialty Retail",
    "industryKey": "specialty-retail",
    "industryDisp": "Specialty Retail",
    "sector": "Consumer Cyclical",
    "sectorKey": "consumer-cyclical",
    "sectorDisp": "Consumer Cyclical",
    "longBusinessSummary": "GameStop Corp., a specialty retailer, provides games and entertainment products through its stores and e-commerce platforms in the United States, Canada, Australia, and Europe. The company sells new and pre-owned gaming platforms; accessories, such as controllers, and gaming headsets; new and pre-owned gaming software; and in-game digital currency, digital downloadable content, and full-game downloads. It sells collectibles comprising apparel, toys, trading cards, gadgets, and other retail products for pop culture and technology 

> Get historical share price data

In [65]:
gamestop = yf.Ticker("GME")
gamestop_info = gamestop.info
print(json.dumps(gamestop_info, indent=4))
gamestop_share_price_data = gamestop.history(period="max")
gamestop_share_price_data.reset_index(inplace=True)
gamestop_share_price_data.head()

Date      Open      High       Low     Close    Volume  \
0 2002-02-13 00:00:00-05:00  1.620129  1.693350  1.603296  1.691667  76216000   
1 2002-02-14 00:00:00-05:00  1.712707  1.716073  1.670625  1.683250  11021600   
2 2002-02-15 00:00:00-05:00  1.683250  1.687458  1.658002  1.674834   8389600   
3 2002-02-19 00:00:00-05:00  1.666418  1.666418  1.578047  1.607504   7410400   
4 2002-02-20 00:00:00-05:00  1.615920  1.662210  1.603296  1.662210   6892800   

   Dividends  Stock Splits  
0        0.0           0.0  
1        0.0           0.0  
2        0.0           0.0  
3        0.0           0.0  
4        0.0           0.0

## 4 - Extracting GameStop Revenue Data Using Webscraping

In [66]:
url = "https://finance.yahoo.com/quote/GME/financials/"
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36',
    'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
    'Accept-Language': 'en-US,en;q=0.5',
    'Referer': 'https://finance.yahoo.com/'
}

data = requests.get(url, headers=headers).text

In [67]:
print(data)

<!doctype html>
<html lang="en-US" theme="auto" data-color-theme-enabled="true" data-color-scheme="auto" class="desktop neo-green dock-upscale">
    <head>
        <meta charset="utf-8" />
        <meta name="oath:guce:consent-host" content="guce.yahoo.com" />
        <link rel="preconnect" href="//s.yimg.com" crossorigin="anonymous"><link rel="preconnect" href="//geo.yahoo.com"/><link rel="preconnect" href="//query1.finance.yahoo.com"/><link rel="preconnect" href="//query2.finance.yahoo.com"/><link rel="preconnect" href="//consent.cmp.oath.com"/><link rel="preload" href="/__rapidworker-1.2.js" as="worker"/><link rel="preconnect" href="https://s.yimg.com/uc/finance/webcore/js/_staticFinProtobuf.adb9bf9ae7922cf2dccf.js"/><link rel="preconnect" href="https://cdn.jsdelivr.net/npm/protobufjs@7.1.2/dist/minimal/protobuf.min.js"/><script>window.finNeoPageStart = Date.now();</script><script>(function(){if(!window.YAHOO){window.YAHOO={}}; window.YAHOO.context={"consent":{"allowContentPersonali

In [68]:
soup = BeautifulSoup(data, 'html.parser')

In [69]:
Revenue_table = soup.find_all("div", class_="table yf-yuwun0")[0]
Revenue_table_header = Revenue_table.find("div", class_="tableHeader yf-yuwun0")
Revenue_table_body = Revenue_table.find("div", class_="tableBody yf-yuwun0")

# Extract column headers
columns = []
for row in Revenue_table.find("div", class_="tableHeader yf-yuwun0").find_all("div", class_="column"):
    columns.append(row.text)
print(columns)

['Breakdown', 'TTM ', '1/31/2025 ', '1/31/2024 ', '1/31/2023 ', '1/31/2022 ']


In [70]:
gamestop_data = pd.DataFrame(columns=columns)

In [71]:
rows_data = []

for row in Revenue_table.find("div", class_="tableBody yf-yuwun0").find_all("div", class_="row"):
    cols = row.find_all("div", class_="column")
    breakdown = cols[0].find("div", class_="rowTitle").text.strip()
    values = [col.text.strip() for col in cols[1:]]
    rows_data.append({
        "Breakdown": breakdown,
        "TTM ": values[0] if len(values) > 0 else None,
        "01/31/2025 ": values[1] if len(values) > 1 else None,
        "02/03/2024 ": values[2] if len(values) > 2 else None,
        "01/28/2023 ": values[3] if len(values) > 3 else None,
        "01/29/2022 ": values[4] if len(values) > 4 else None
    })

gamestop_data = pd.DataFrame(rows_data)
gamestop_data.head()

Breakdown       TTM  01/31/2025  02/03/2024  01/28/2023   \
0      Total Revenue  3,847,500   3,823,000   5,272,800   5,927,200   
1    Cost of Revenue  2,691,000   2,709,100   3,978,600   4,555,100   
2       Gross Profit  1,156,500   1,113,900   1,294,200   1,372,100   
3  Operating Expense  1,011,400   1,130,400   1,323,900   1,681,000   
4   Operating Income    145,100     -16,500     -29,700    -308,900   

  01/29/2022   
0   6,010,700  
1   4,662,900  
2   1,347,800  
3   1,709,600  
4    -361,800

In [78]:
gamestop_data.tail()

Breakdown     TTM  01/31/2025  02/03/2024   \
27  Total Unusual Items Excluding Goodwill  -14,500      -9,700      -4,800   
28                     Total Unusual Items  -14,500      -9,700      -4,800   
29                       Normalized EBITDA  184,400      32,100      31,300   
30                      Tax Rate for Calcs        0           0           0   
31             Tax Effect of Unusual Items  -617.10     -417.10      -1,008   

   01/28/2023  01/29/2022   
27      -2,700      -6,700  
28      -2,700      -6,700  
29    -244,500    -277,900  
30           0           0  
31        -567     -241.20

## 5 - Tesla Stock and Revenue Dashboard

In [72]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [73]:
def make_graph(stock_data, revenue_data, stock):
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        subplot_titles=("Historical Share Price", "Historical Revenue"),
                        vertical_spacing = .3)
    stock_data_specific = stock_data[stock_data.Date <= '2021-06-14']
    revenue_data_specific = revenue_data[revenue_data.Date <= '2021-04-30']
    fig.add_trace(go.Scatter(x=pd.to_datetime(stock_data_specific.Date, infer_datetime_format=True),
                             y=stock_data_specific.Close.astype("float"), name="Share Price"), row=1, col=1)
    fig.add_trace(go.Scatter(x=pd.to_datetime(revenue_data_specific.Date, infer_datetime_format=True),
                             y=revenue_data_specific.Revenue.astype("float"), name="Revenue"), row=2, col=1)
    fig.update_xaxes(title_text="Date", row=1, col=1)
    fig.update_xaxes(title_text="Date", row=2, col=1)
    fig.update_yaxes(title_text="Price ($US)", row=1, col=1)
    fig.update_yaxes(title_text="Revenue ($US Millions)", row=2, col=1)
    fig.update_layout(showlegend=False,
                     height=900,
                     title=stock,
                     xaxis_rangeslider_visible=True)
    fig.show()

> Function to transform revenue data from wide to long format

In [74]:
def prepare_revenue_data(revenue_df):
    # Filter to get only "Total Revenue" row
    total_revenue = revenue_df[revenue_df['Breakdown'].str.contains('Total Revenue', case=False, na=False)]

    if total_revenue.empty:
        print("Warning: 'Total Revenue' not found in data")
        return pd.DataFrame(columns=['Date', 'Revenue'])

    # Get the first row (Total Revenue)
    revenue_row = total_revenue.iloc[0]

    # Extract date columns (skip 'Breakdown' and 'TTM')
    date_columns = [col for col in revenue_df.columns if col not in ['Breakdown', 'TTM', 'TTM ']]
    dates = []
    revenues = []

    for col in date_columns:
        date_str = col.strip()
        revenue_str = str(revenue_row[col]).strip().replace(',', '')

        # Convert date string to datetime
        try:
            date = pd.to_datetime(date_str)
            dates.append(date)

            # Convert revenue to float (handle empty or '-' values)
            if revenue_str and revenue_str != '-' and revenue_str != 'None':
                revenues.append(float(revenue_str) / 1000)
            else:
                revenues.append(None)
        except:
            continue

    # Create DataFrame
    revenue_data_long = pd.DataFrame({
        'Date': dates,
        'Revenue': revenues
    })

    # Sort by date
    revenue_data_long = revenue_data_long.sort_values('Date').reset_index(drop=True)

    return revenue_data_long

In [75]:
print("Creating Tesla Dashboard...")

# Prepare Tesla stock data (already in correct format)
tesla_stock = tesla_share_price_data[['Date', 'Open', 'High', 'Low', 'Close', 'Volume', 'Dividends', 'Stock Splits']].copy()

# Prepare Tesla revenue data
tesla_revenue = prepare_revenue_data(tesla_data)
print("\nTesla Revenue Data:")
print(tesla_revenue)

# Create Tesla dashboard
make_graph(tesla_stock, tesla_revenue, 'Tesla')

Creating Tesla Dashboard...

Tesla Revenue Data:
        Date  Revenue
0 2021-12-31  53823.0
1 2022-12-31  81462.0
2 2023-12-31  96773.0
3 2024-12-31  97690.0


/tmp/ipython-input-3084507138.py:7: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.

/tmp/ipython-input-3084507138.py:9: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.



## 6 - GameStop Stock and Revenue Dashboard

In [76]:
print("\nCreating GameStop Dashboard...")

# Prepare GameStop stock data (already in correct format)
gamestop_stock = gamestop_share_price_data[['Date', 'Open', 'High', 'Low', 'Close', 'Volume', 'Dividends', 'Stock Splits']].copy()

# Prepare GameStop revenue data
gamestop_revenue = prepare_revenue_data(gamestop_data)
print("\nGameStop Revenue Data:")
print(gamestop_revenue)

# Create GameStop dashboard
make_graph(gamestop_stock, gamestop_revenue, 'GameStop')


Creating GameStop Dashboard...

GameStop Revenue Data:
        Date  Revenue
0 2022-01-29   6010.7
1 2023-01-28   5927.2
2 2024-02-03   5272.8
3 2025-01-31   3823.0


/tmp/ipython-input-3084507138.py:7: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.

/tmp/ipython-input-3084507138.py:9: UserWarning:

The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.

